In [1]:
import pandas as pd
import numpy as np
import os
from tqdm import tqdm
from datetime import datetime

In [2]:
now = datetime.now()
now = now.replace(month=1, day=5)
now

datetime.datetime(2024, 1, 5, 11, 55, 13, 99135)

In [3]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fsecs = range(midnight, next_day, 5) # fsecs : unix time by Five SECondS
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS

In [4]:
history = pd.read_csv('../Data/tables/history.csv', index_col=0)
m = 105
present_time = fmins[m]

# - 아래 절차를 5초마다 반복
for fsec in range(midnight, present_time + 1, 5): # fsec : unix time by Five SECond
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    # move = time2move[fsec]
    move = pd.read_csv(f'../Data/tables/move/move_{fsec}.csv', index_col=0)
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로변호, 종료유닉스타임)만 수집 : B
    recent_histories = [group.iloc[-1:] for _, group in history[history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들
    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    move = move.drop_duplicates()
    # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        if isinstance(movement, pd.DataFrame): # movement가 존재할 경우 그걸 그대로 씀.
            pass
        else: 
            movement = pd.DataFrame()
    except NameError: # movement가 존재하지 않는 경우 생성
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - 3600을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - 3600]
    movement = movement.sort_values(by=['start_unix','inter_no','phas_A','phas_B']).reset_index(drop=True)

display(movement)

inter_no  phas_A  phas_B  move_A  move_B  start_unix
0         177       1       1       8       4  1704408330
1         177       2       2       7       3  1704408330
2         177       3       3      17      18  1704408330
3         177       4       4       5       1  1704408330
4         201       1       1       8       3  1704408330
..        ...     ...     ...     ...     ...         ...
700       178       4       4       6       1  1704411830
701       201       1       1       8       3  1704411850
702       201       4       4       6       1  1704411850
703       201       5       5       7       4  1704411850
704       206       2       2      17      18  1704411880

[705 rows x 6 columns]

In [5]:
def make_splits(plan):
    # split, isplit : A,B 분리 혹은 통합시 사용될 수 있는 딕셔너리 
    splits = {} # splits maps (inter_no, start_hour, start_minute) to split 
    for i, row in plan.iterrows():
        inter_no = row.inter_no
        start_hour = row.start_hour
        start_minute = row.start_minute
        cycle = row.cycle
        cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
        cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
        splits[(inter_no, start_hour, start_minute)] = {} # split maps (phas_A, phas_B) to k
        k = 0
        for t in range(cycle):
            new_phas_A = len(cums_A[cums_A < t]) + 1
            new_phas_B = len(cums_B[cums_B < t]) + 1
            if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
                k += 1
            phas_A = new_phas_A
            phas_B = new_phas_B
            splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k

    isplits = {} # the inverse of splits
    for i in splits:
        isplits[i] = {splits[i][k]:k for k in splits[i]} # isplit maps k to (phas_A, phas_B)
    return splits, isplits

def make_timetable(plan):
    # timetable
    timetable = plan[['start_hour', 'start_minute']].drop_duplicates()
    timetable['start_seconds'] = midnight + timetable['start_hour'] * 3600 + timetable['start_minute'] * 60
    return timetable

# inter2node
inter_node = pd.read_csv('../Data/tables/inter_node.csv', index_col=0)
inter_node = inter_node[inter_node.inter_type=='parent']
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))

hours = np.array(range(midnight - 7200, next_day + 1, 3600)) # 정각에 해당하는 시각들 목록

In [6]:
def calculate_DS(rhist, curr_unix, hours, timetable):
    program_starts = np.array(timetable.start_seconds)
    idx = (program_starts <= present_time).sum() - 1
    program_start = program_starts[idx]
    if list(hours[hours <= curr_unix]):
        ghour_lt_curr_unix = hours[hours <= curr_unix].max() # the greatest hour less than or equal to curr_unix
    else:
        ghour_lt_curr_unix = program_start
    start_unixes = rhist.start_unix.unique()
    start_unixes_lt_ghour = np.sort(start_unixes[start_unixes < ghour_lt_curr_unix]) # start unixes less than ghour_lt_curr_unix
    # 기준유닉스(base_unix) : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 start_unix
    if len(start_unixes_lt_ghour) > 5:
        base_unix = start_unixes_lt_ghour[-5]
    # start_unixes_lt_ghour의 길이가 5 미만일 경우에는 맨 앞 start_unix로 base_unix를 지정
    else:
        base_unix = rhist.start_unix.min()
    D_n = curr_unix - base_unix
    S_n_durs = rhist[(rhist.start_unix > base_unix) & (rhist.start_unix <= curr_unix)] \
        [[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
    S_n = S_n_durs.values.sum() // 2
    return D_n, S_n

In [7]:
def load_prow(plan, timetable, inter_no, time):
    '''
    load planned row
    '''
    # 프로그램 시작시각
    program_starts = np.array(timetable.start_seconds)
    idx = (program_starts <= time).sum() - 1
    program_start = program_starts[idx]

    # 최근 프로그램 시작시각에 대한 신호계획
    start_hour = timetable.iloc[idx].start_hour
    start_minute = timetable.iloc[idx].start_minute
    prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
    return program_start, prow

In [8]:
def make_rhistory(plan, timetable, history, present_time, adder):
    # 1. 조회시점의 유닉스 타임 이전의 신호이력 수집
    rhistory = history.copy() # recent history
    rhistory = rhistory[(rhistory.end_unix <= present_time) & (rhistory.end_unix > present_time - 9000)] # 두 시간 반 전부터 현재까지의 신호이력을 가져옴. 9000 = 3600 * 2.5

    # rhistory에 모든 교차로번호가 존재하지 않으면 해당 교차로번호에 대한 신호이력을 추가함 (at 최근 프로그램 시작시각)
    whole_inter_nos = sorted(history.inter_no.unique())
    recent_inter_nos = sorted(rhistory.inter_no.unique())
    if not whole_inter_nos==recent_inter_nos:
        for inter_no in set(whole_inter_nos) - set(recent_inter_nos):
            program_start, prow = load_prow(plan, timetable, inter_no, present_time - 9000)
            cycle = prow.cycle.iloc[0]
            row1 = prow.drop(['start_hour', 'start_minute'], axis=1).copy()
            row2 = prow.drop(['start_hour', 'start_minute'], axis=1).copy()
            # prow에서 필요한 부분을 rhistory에 추가
            row1['end_unix'] = program_start
            row2['end_unix'] = program_start + cycle
            rhistory = pd.concat([rhistory, row1, row2]).reset_index(drop=True)
    # present_time + adder 의 시각에 한 주기의 신호 추가
    for inter_no in set(whole_inter_nos):
        program_start, prow = load_prow(plan, timetable, inter_no, present_time)
        cycle = prow.cycle.iloc[0]
        row3 = prow.drop(['start_hour', 'start_minute'], axis=1).copy()
        # prow에서 필요한 부분을 rhistory에 추가
        row3['end_unix'] = present_time + adder
        rhistory = pd.concat([rhistory, row3]).reset_index(drop=True)

    # 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
    # - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
    for i, row in rhistory.iterrows():
        inter_no = row.inter_no
        end_unix = row.end_unix
        elapsed_time = row[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]].sum() // 2 # 현시시간 합
        # 이전 유닉스 존재하지 않음 : 현시시간 합의 차
        start_unix = end_unix - elapsed_time
        pre_rows = history[:i] # previous rows
        if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
            pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
            # 이전 유닉스 존재, abs < 10 : 이전 유닉스
            if abs(pre_unix - start_unix) < 10:
                start_unix = pre_unix
            # 이전 유닉스 존재, abs >=10 : 현시시간 합의 차
            else:
                pass
        rhistory.loc[i, 'start_unix'] = start_unix 
    rhistory[rhistory.isna()] = 0
    rhistory['start_unix'] = rhistory['start_unix'].astype(int)
    rhistory = rhistory[['inter_no', 'start_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle']]
    return rhistory
adder = 600

In [9]:
def processing(plan, rhistory, timetable, hours):
    rhists = []
    for inter_no in sorted(rhistory.inter_no.unique()):
        rhist = rhistory.copy()[rhistory.inter_no==inter_no]
        rhist = rhist.drop_duplicates(subset=['start_unix']).reset_index(drop=True)

        # D_n 및 S_n 값 정의
        rhist['D_n'] = 0 # D_n : 시간차이
        rhist['S_n'] = 0 # S_n : 현시시간합
        for n in range(len(rhist)):
            curr_unix = rhist.iloc[n].start_unix # current start_unix
            rhist.loc[n, ['D_n', 'S_n']] = calculate_DS(rhist, curr_unix, hours, timetable)

        # 이전시각, 현재시각
        prev_unix = rhist.loc[0, 'start_unix'] # previous start_unix
        curr_unix = rhist.loc[1, 'start_unix'] # current start_unix

        # rhist의 마지막 행에 도달할 때까지 반복
        while True:
            n = rhist[rhist.start_unix==curr_unix].index[0]
            cycle = rhist.loc[n, 'cycle']
            D_n = rhist.loc[n, 'D_n']
            S_n = rhist.loc[n, 'S_n']
            # 참값인 경우
            if (abs(D_n - S_n) <= 5):
                pass
            # 참값이 아닌 경우
            else:
                # 2-1-1. 결측치 처리 : 인접한 두 start_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단, 신호계획의 현시시간으로 "대체"
                if curr_unix - prev_unix >= 2 * cycle:
                    # prev_unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
                    # (curr_unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
                    while curr_unix - prev_unix > cycle:
                        prev_unix += cycle
                        # 신호 계획(prow) 불러오기
                        start_seconds = np.array(timetable.start_seconds)
                        idx = (start_seconds <= prev_unix).sum() - 1
                        start_hour = timetable.iloc[idx].start_hour
                        start_minute = timetable.iloc[idx].start_minute
                        prow = plan.copy()[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                        # prow에서 필요한 부분을 rhist에 추가
                        prow['start_unix'] = prev_unix
                        prow = prow.drop(['start_hour', 'start_minute', 'offset'], axis=1)
                        cycle = prow.iloc[0].cycle
                        rhist = pd.concat([rhist, prow])
                        rhist = rhist.sort_values(by='start_unix').reset_index(drop=True)
                        n += 1

                # 2-1-2. 이상치 처리 : 비율에 따라 해당 행을 "삭제"(R_n <= 0.5) 또는 "조정"(R_n > 0.5)한다
                R_n = (curr_unix - prev_unix) / cycle # R_n : 비율
                # R_n이 0.5보다 작거나 같으면 해당 행을 삭제
                if R_n <= 0.5:
                    rhist = rhist.drop(index=n).reset_index(drop=True)
                    if n >= rhist.index[-1]:
                        break
                    # 행삭제에 따른 curr_unix, R_n 재정의
                    curr_unix = rhist.loc[n, 'start_unix']
                    R_n = (curr_unix - prev_unix) / cycle # R_n : 비율

                # R_n이 0.5보다 크면 해당 행 조정 (비율을 유지한 채로 현시시간 대체)
                if R_n > 0.5:
                    # 신호 계획(prow) 불러오기
                    start_seconds = np.array(timetable.start_seconds)
                    idx = (start_seconds <= curr_unix).sum() - 1
                    start_hour = timetable.iloc[idx].start_hour
                    start_minute = timetable.iloc[idx].start_minute
                    prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                    # 조정된 현시시간 (prow에 R_n을 곱하고 정수로 바꿈)
                    adjusted_dur = prow.copy()[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] * R_n
                    int_parts = adjusted_dur.iloc[0].apply(lambda x: int(x))
                    frac_parts = adjusted_dur.iloc[0] - int_parts
                    difference = round(adjusted_dur.iloc[0].sum()) - int_parts.sum()
                    for _ in range(difference): # 소수 부분이 가장 큰 상위 'difference'개의 값에 대해 올림 처리
                        max_frac_index = frac_parts.idxmax()
                        int_parts[max_frac_index] += 1
                        frac_parts[max_frac_index] = 0  # 이미 처리된 항목은 0으로 설정
                    # rhist에 조정된 현시시간을 반영
                    rhist.loc[n, [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] = int_parts.values
                    rhist.loc[n, 'cycle'] = int_parts.sum().sum() // 2

            if n >= rhist.index[-1]:
                break
            prev_unix = curr_unix
            curr_unix = rhist.loc[n+1, 'start_unix']

        # 생략해도 무방할 코드
        rhist = rhist.reset_index(drop=True)
        rhist = rhist.sort_values(by=['start_unix'])

        # D_n 및 S_n 값 재정의
        for n in range(len(rhist)):
            curr_unix = rhist.iloc[n].start_unix # current start_unix
            rhist.loc[n, ['D_n', 'S_n']] = calculate_DS(rhist, curr_unix, hours, timetable)
        rhists.append(rhist)
    rhists = pd.concat(rhists).sort_values(by=['start_unix','inter_no'])
    rhists = rhists[rhists.start_unix >= present_time - 3600]
    rhists = rhists.drop(columns=['D_n', 'S_n'])
    return rhists

In [10]:
def make_hrhists(rhists, isplits, timetable):
    # 계층화된 형태로 변환
    hrhists = [] # hierarchied recent history
    for i, row in rhists.iterrows():
        inter_no = row.inter_no
        start_unix = row.start_unix

        ind = (timetable['start_seconds'] <= row.start_unix).sum() - 1
        start_hour = timetable.iloc[ind].start_hour
        start_minute = timetable.iloc[ind].start_minute
        isplit = isplits[(inter_no, start_hour, start_minute)]
        phas_As = [isplit[j][0] for j in isplit.keys()]
        phas_Bs = [isplit[j][1] for j in isplit.keys()]
        durs_A = row[[f'dura_A{j}' for j in range(1,9)]]
        durs_B = row[[f'dura_B{j}' for j in range(1,9)]]
        durations = []
        for j in range(1, len(isplit)+1):
            ja = isplit[j][0]
            jb = isplit[j][1]
            if ja == jb:
                durations.append(min(durs_A[ja-1], durs_B[jb-1]))
            else:
                durations.append(abs(durs_A[ja-1] - durs_B[ja-1]))
        new_rows = pd.DataFrame({'inter_no':[inter_no] * len(durations), 'start_unix':[start_unix] * len(durations),
                                'phas_A':phas_As, 'phas_B':phas_Bs, 'duration':durations})
        hrhists.append(new_rows)
    hrhists = pd.concat(hrhists)
    hrhists = hrhists.sort_values(by = ['start_unix', 'inter_no', 'phas_A', 'phas_B']).reset_index(drop=True)
    return hrhists

In [11]:
def update_movement(hrhists, movement, movements):
    # 중복을 제거하고 (inter_no, start_unix) 쌍을 만듭니다.
    hrhists_inter_unix = set(hrhists[['inter_no', 'start_unix']].drop_duplicates().itertuples(index=False, name=None))
    movement_inter_unix = set(movement[['inter_no', 'start_unix']].drop_duplicates().itertuples(index=False, name=None))

    # hrhists에는 있지만 movement에는 없는 (inter_no, start_unix) 쌍을 찾습니다.
    missing_in_movement = hrhists_inter_unix - movement_inter_unix

    # 새로운 행들을 생성합니다.
    new_rows = []
    if missing_in_movement:
        for inter_no, start_unix in missing_in_movement:
            # movements에서 해당 inter_no의 데이터를 찾습니다.
            new_row = movements[movements['inter_no'] == inter_no].copy()
            # start_unix 값을 설정합니다.
            new_row['start_unix'] = start_unix
            new_rows.append(new_row)

        # 새로운 데이터프레임을 생성하고 기존 movement 데이터프레임과 합칩니다.
        new_movement = pd.concat(new_rows, ignore_index=True)
        movement_updated = pd.concat([movement, new_movement], ignore_index=True)
    else:
        movement_updated = movement
    return movement_updated

In [13]:
def make_histid(present_time, hrhists, movement_updated, inter2node, matching):
    # movements and durations
    movedur = pd.merge(hrhists, movement_updated, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B'])
    movedur = movedur.sort_values(by=['start_unix', 'inter_no', 'phas_A','phas_B'])
    movedur = movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]

    # 이동류 매칭 테이블에서 진입id, 진출id를 가져와서 붙임.
    for i, row in movedur.iterrows():
        inter_no = row.inter_no
        start_unix = row.start_unix
        # incoming and outgoing edges A
        move_A = row.move_A
        if move_A in [17, 18]:
            inc_edge_A = np.nan
            outhedge_A = np.nan
        else:
            match_A = matching[(matching.inter_no == inter_no) & (matching.move_no == move_A)].iloc[0]
            inc_edge_A = match_A.inc_edge
            out_edge_A = match_A.out_edge
        movedur.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge_A, out_edge_A]
        # incoming and outgoing edges B
        move_B = row.move_B
        if move_B in [17, 18]:
            inc_edge_B = np.nan
            out_edge_B = np.nan
        else:
            match_B = matching[(matching.inter_no == inter_no) & (matching.move_no == move_B)].iloc[0]
            inc_edge_B = match_B.inc_edge
            out_edge_B = match_B.out_edge
        movedur.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge_B, out_edge_B]

    # 이동류 컬럼 제거
    movedur = movedur.drop(['move_A', 'move_B'], axis=1)

    histid = movedur.copy() # history with edge ids (incoming and outgoing edge ids)
    histid['node_id'] = histid['inter_no'].map(inter2node)
    histid = histid[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'duration', 'inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']]
    histid_start = present_time - 600
    histid = histid[histid.start_unix > histid_start]
    return histid

In [14]:
def preprocess(m):
   '''
   통합테이블(histid)를 만드는 함수

   input : m
    - m ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
    - present_time = fmins[m] : 현재시점

   output : histid (통합테이블, HISTory with edge_IDs)
    - 컬럼 : inter_no, node_id, start_unix, phas_A, phas_B, duration, inc_edge_A, out_edge_A, inc_edge_B, out_edge_B

   주요 데이터, 중간산출물 및 결과물 :
   # 데이터
    - history : 신호이력 (inter_no, end_unix, dura_Aj, dura_Bj, cycle, offset)
    - plan : 신호계획 (inter_no, start_hour, start_minute, dura_Aj, dura_Bj cycle, offset)
   # 중간산출물
    - rhists (recent history)
       - history에서 현재 시각 이전의 데이터를 가져옴.
       - end_unix를 start_unix로 변환
       - 참값판단 프로세스(결측·이상치 처리)
       - 컬럼 : inter_no, start_unix, dura_Aj, dura_Bj, cycle
    - hrhists (hierarchized recent history)
       - rhists를 계층화
       - 컬럼 : inter_no, start_unix, phas_A, phas_B, duration
    - movements
       - 각 교차로에 대하여 현시별로 이동류를 정해놓음.
       - join시 사용하기 위함.
       - 한 번 만들어놓고 두고두고 사용함.
       - 컬럼 : inter_no, phas_A, phas_B, move_A, move_B
    - movement
       - 현재 시점에서의 이동류정보
       - 컬럼 : inter_no, phas_A, phas_B, move_A, move_B, start_unix
    - movement_updated
       - movement와 hrhists를 join하기 전에, movement에는 없지만 hrhists에는 있는 start_unix에 대한 이동류 정보를 가져와 movement에 붙임
       - 이동류정보는 앞서 정의한 movements에서 가져옴.
       - 컬럼 : inter_no, phas_A, phas_B, move_A, move_B, start_unix
    - movedur
       - hrhists와 movement_updated를 join
       - 컬럼 : inter_no, phas_A, phas_B, move_A, move_B, start_unix, duration
   # 결과 : histid
       - 신호생성에 직접적으로 사용되는 데이터프레임
       - 컬럼 : inter_no, node_id, start_unix, phas_A, phas_B, duration, inc_edge_A, out_edge_A, inc_edge_B, out_edge_B
       - 한글컬럼 : 교차로번호, 노드id, 시작유닉스, A현시번호, B현시번호, 현시시간, 진입엣지(A), 진출엣지(A), 진입엣지(B), 진출엣지(B)
   '''
   midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
   next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
   fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
   # 현재시각
   present_time = fmins[m]
   print(datetime.fromtimestamp(present_time))
   # 사용할 표준 테이블 목록
   plan = pd.read_csv('../Data/tables/plan.csv', index_col=0)
   history = pd.read_csv('../Data/tables/history.csv', index_col=0)
   matching = pd.read_csv('../Intermediates/matching.csv', index_col=0)
   # 참고할 딕셔너리, 데이터프레임, 리스트 등 목록
   splits, isplits = make_splits(plan)
   timetable = make_timetable(plan)
   inter_node = pd.read_csv('../Data/tables/inter_node.csv', index_col=0)
   inter_node = inter_node[inter_node.inter_type=='parent']
   inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
   hours = np.array(range(midnight - 7200, next_day + 1, 3600)) # 정각에 해당하는 시각들 목록
   # rhistory, rhists, hrhists
   adder = 600
   rhistory = make_rhistory(plan, timetable, history, present_time, adder)
   rhists = processing(plan, rhistory, timetable, hours)
   hrhists = make_hrhists(rhists, isplits, timetable)
   # movements, movement, movement_updated
   movements = pd.read_csv('../Intermediates/movements.csv')
   movement = pd.read_csv(f'../Intermediates/movement/movement_{present_time}.csv', index_col=0)
   movement_updated = update_movement(hrhists, movement, movements)
   # movedur
   movedur = pd.merge(movement_updated, hrhists, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B']) # movements and durations
   movedur = movedur.sort_values(by=['start_unix', 'inter_no', 'phas_A','phas_B'])
   movedur = movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]
   # histid
   histid = make_histid(present_time, hrhists, movement_updated, inter2node, matching)
   histid.to_csv(f'../Intermediates/histid/histid_{fmins[m]}.csv')
   return histid

In [15]:
preprocess(105)
preprocess(106)

2024-01-05 08:45:00
2024-01-05 08:50:00


inter_no node_id  start_unix  phas_A  phas_B  duration     inc_edge_A  \
655       202      i9  1704411610       1       1        46   571510152_02   
656       202      i9  1704411610       2       2       114            NaN   
657       175      i0  1704411629       1       1        40  -571542797_02   
658       175      i0  1704411629       2       2        42  -571500487_01   
659       175      i0  1704411629       3       3        29   571545870_02   
..        ...     ...         ...     ...     ...       ...            ...   
871       201      i8  1704412640       5       5        17   571500583_01   
872       206      i7  1704412660       1       1        25  -571511538_02   
873       206      i7  1704412660       2       2        25            NaN   
874       206      i7  1704412660       3       3        15  -571511538_02   
875       206      i7  1704412660       4       4        15            NaN   

        out_edge_A     inc_edge_B       out_edge_B  
655  -571510152_01   571510152_01  571510152_01.65  
656  -571510152_01            NaN              NaN  
657   571500487_01  -571500487_01     571542797_02  
658   571545870_01  -571542797_02     571510153_01  
659   571510153_01   571545870_02     571542797_02  
..             ...            ...              ...  
871   571500617_01   571500583_01     571500569_01  
872   571542073_02   571542073_01     571511538_02  
873   571542073_02            NaN              NaN  
874   571542073_02   571542073_01     571511538_02  
875   571542073_02            NaN              NaN  

[221 rows x 10 columns]

In [16]:
# for m in range(30, 288):
#     print(m)
#     histid = preprocess(m)